In [1]:
import geopandas as gpd
import pandas as pd
import numpy as np
import folium

In [3]:
df = pd.read_csv('/data/visualize-data.csv')
df.head()
# df.dtypes

FileNotFoundError: [Errno 2] No such file or directory: '/data/visualize-data.csv'

In [3]:
df = df [['fire_size', 'latitude', 'longitude', 'state', 'stat_cause_descr']]
x = len(df)

In [30]:
df.head(15)

fire_size   latitude   longitude state stat_cause_descr
36     1420.0000  33.241800 -104.912200    NM        Lightning
117    1330.2000  27.163610  -81.523340    FL   Debris Burning
234    1400.0000  29.940000  -93.665660    LA            Arson
633    1600.0000  46.661700 -108.531700    MT        Lightning
654    1500.0000  39.833333  -98.833333    KS   Debris Burning
734   10610.0000  31.338889 -110.545833    AZ    Miscellaneous
1146   1800.0000  45.650833 -106.141111    MT        Lightning
1304   2613.0000  36.803900  -96.222200    OK            Arson
1393   1077.0000  45.442222 -114.557500    ID        Lightning
1441   8330.0000  26.033330  -81.300000    FL        Lightning
1624   1221.0000  40.050000 -105.050000    CO        Lightning
1629   3073.0000  47.428900 -114.391400    MT        Lightning
1855  19520.0000  45.270000 -114.805000    ID        Lightning
1961   1766.0000  39.551900 -119.665200    NV    Miscellaneous
2034   5774.2002  45.806800 -106.119700    MT        Lightning

In [46]:
df = df.loc[df['fire_size'] > 1000]

In [44]:
m = folium.Map(location = [37.256500, -122.027153],
               zoom_start = 6)

small_wildfires = folium.FeatureGroup(name = '< 10000 Acres')
medium_wildfires = folium.FeatureGroup(name = '10,000 - 50,000 Acres')
large_wildfires = folium.FeatureGroup(name = '50,000 - 100,000 Acres')
xl_wildfires = folium.FeatureGroup(name = '> 100,000 Acres')


for i, v in df.iterrows():
    fire_size = float(v['fire_size'])
    
    popup = """
    Size (Acres) : <b>%s</b><br>
    State : <b>%s</b><br>
    Cause : <b>%s</b><br>
    """ % (v['fire_size'], v['state'], v['stat_cause_descr'])
    
    
    if fire_size < 10000:
        folium.CircleMarker(location = [v['latitude'], v['longitude']],
                           radius = np.log(fire_size) * 0.8,
                           weight = 0,
                           tooltip = popup,
                           color = '#ffeda0',
                           fill_color = '#ffeda0',
                           fill_opacity = 0.7,
                           fill = True).add_to(small_wildfires)
        
    if fire_size in range(10000, 50000):
        folium.CircleMarker(location = [v['latitude'], v['longitude']],
                           radius = np.log(fire_size),
                           weight = 0,
                           tooltip = popup,
                           color = '#feb24c',
                           fill_color = '#feb24c',
                           fill_opacity = 0.7,
                           fill = True).add_to(medium_wildfires)
    
    if fire_size in range(50000, 100000):
        folium.CircleMarker(location = [v['latitude'], v['longitude']],
                           radius = np.log(fire_size) * 1.5,
                           weight = 0,
                           tooltip = popup,
                           color = '#fc4e2a',
                           fill_color = '#fc4e2a',
                           fill_opacity = 0.7,
                           fill = True).add_to(large_wildfires)

    if fire_size > 100000:
        folium.CircleMarker(location = [v['latitude'], v['longitude']],
                           radius = np.log(fire_size) * 2,
                           weight = 0,
                           tooltip = popup,
                           color = '##b10026',
                           fill_color = '#b10026',
                           fill_opacity = 0.7,
                           fill = True).add_to(xl_wildfires)

small_wildfires.add_to(m)
medium_wildfires.add_to(m)
large_wildfires.add_to(m)
xl_wildfires.add_to(m)
folium.LayerControl(collapsed = False).add_to(m)

m.save(r'visualizations.html')
m